# 05-Isochrones

What if, starting from a point, we could navigate adjacent streets and see how far we can go in a limited amount of time? It could give us an idea of the connectivity between the school and its belonging city and about the city itself. Also, we could compare different means of transport (walk, bike and car) and streets viability in terms of time.

The aim of this notebook is to propose an isochrone interactive visualization through folium. An isochrone map in geography and urban planning is a map that depicts the area accessible from a point within a certain time threshold. 

In our case, these thresholds will be 5, 10, 15 and 20 minutes, illustrated through a gradient starting from yellow to dark red. 

In [3]:
# Libraries
from platform import mac_ver
import pandas as pd
import geopandas as gpd
import networkx as nx
import osmnx as ox
import folium
from shapely.geometry import Point

Let's load school's data, with their position. We can grasp the name, the address and the municipality and save it as description field inside schools dataframe. This column is then saved as json file, with the index of the dataframe as keys, in order to retrieve schools visualizations' path inside the website. This means that each school has its own number. 

In [4]:
# Reading school files
schools = gpd.read_file(
    "../data/Trentino/schools/schools.geojson", geometry="geometry")

schools['Descrizione'] = schools['Nome']+" - "+ schools['Indirizzo'] +", " + schools['Comune']

# Save list for the website, in order to choose the school
schools['Descrizione'].to_json("../data/schools_list_for_select.json")

We will test the following code on the first school inside the dataframe, setting network types, trip times and colors. 

In [5]:
schools.drop(["Descrizione"], axis=1, inplace=True)
network_type = ['walk', 'bike', 'drive_service']
trip_times = [5, 10, 15, 20]  # in minutes
colors = ['#fecc5c', '#fd8d3c', '#f03b20', '#bd0026']
colors.reverse()

The following two functions are necessary for:

* getting the graph network around a specific place (shapely point), with the specified network type (`get_graph()` function). Also, the graph needs to be projected with the 4326 CRS in order to be properly represented;
* obtaining the central node of our isochrone. Since not all schools may be reconducted to a specific street, we search for the nearest node to the place specified on a street (function `get_center_node()`). 

In [6]:
def get_graph(place, net_type):
    # Get the graph with the specified network type around a place
    G = ox.graph_from_point((place.y, place.x), network_type=net_type)

    # Project the graph to EPSG7
    G = ox.project_graph(G, to_crs="EPSG:4326")
    return G


def get_center_node(G, place):
    center_node = ox.nearest_nodes(G, place.x, place.y)
    return center_node

We can start by plotting isochrones considering the street network around a starting point. We center the map around the school, then for every trip time and color, a subgraph is computed, centered around the school, and as extended as the maximum time we want to spend in reaching specific places. The subgraph, starting from the furthest streets, is added to the map with a dark color at first and yellow at the end. Basically, streets colours are drawn one over another. In the end, the school marker is added. 

In [7]:
# ROUTE ISOCHRONES
def get_folium_route_time_distance_map(G, place, trip_times, colors, index):
    # Creating the map
    map = folium.Map(location=(place.y, place.x),
                     tiles='cartodbpositron', zoom_start=14)

    # Getting the closest node point in G to the place
    center_node = get_center_node(G, place)

    # Compute the subnetwork of streets reachable in every trip time
    # (from furthest to closest)
    for trip_time, color in zip(sorted(trip_times, reverse=True), colors):
        subgraph = nx.ego_graph(G, center_node,
                                radius=trip_time, distance='time')
        ox.plot_graph_folium(subgraph, graph_map=map,
                             color=color)

    folium.Marker([place.y, place.x],
                  icon=folium.map.Icon(prefix='fa',
                                       icon='graduation-cap',
                                       color="red"),
                  popup=folium.Popup(folium.Html("<b>"+schools.loc[index, 'Nome'] + "</b><br>"+
                                                 schools.loc[index, 'Istituto']+ "<br>"+ 
                                                 schools.loc[index, 'Comune']+"<br>"+
                                                 schools.loc[index, 'Indirizzo'],
                                                 script=True), max_width=200),
                  tooltip=schools.loc[index, 'Nome']).add_to(map)
    # Adjusting map boundaries
    map.fit_bounds(map.get_bounds())
    return map

*Notice that for every network type (i.e. means of transport) a different map has to be made, since OSM Network x function `ox.plot_graph_folium()` allows just to add the plot to an existing map, but not as one of its layers. A possible improvement could be to create this type of map by layering on the timing or the transport means.*

Let's try to plot some of them for the Liceo Classico Arcivescovile in Trento:

In [8]:
# Trying to set the correct zoom for route isochrones
index = 382
get_folium_route_time_distance_map(get_graph(schools.loc[index, 'geometry'], "walk"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors, 
                                   index)

By walking we can reach Le Albere, San Giuseppe and San Pio X district. Let's inspect with car:

In [9]:
get_folium_route_time_distance_map(get_graph(schools.loc[index, 'geometry'], "drive_service"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors, 
                                   index)

The number of streets drastically reduces when moving from Arcivescovile to Trento streets. It expands to Bolghera district, but since Trento is composed mostly by one way streets, it is pretty obvious that the car viability is slower and more limited than walking. Let's try with the bike:

In [10]:
get_folium_route_time_distance_map(get_graph(schools.loc[index, 'geometry'], "bike"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors, 
                                   index)

When switching to the bike, the isochrone fills with streets! Compared to walking, the centre, Piedicastello and Bolghera are reached, leading to a more spread view of Trento's streets. 

A variant of this type of isochrone are **polygon isochrones**, which represent the same information considering the reachable area, instead of streets. The function `get_folium_isochrone_map()`, starting from a central node, creates a subgraph, creates a bounding polygon as convex_hull and in the end, differences between the external and internal polygons are computed to avoid colors' overlapping.

In [11]:
# POLYGONS ISOCHRONES
def style(feature):
    return {
        'fillColor': feature['properties']['color'],
        'color': feature['properties']['color'],
        'opacity': 0.5,
        'weight': 1
    }

# make the isochrone polygons
def get_folium_isochrone_map(G, place, trip_times, colors):
    isochrone_polys = []
    center_node = get_center_node(G, place)
    for trip_time in sorted(trip_times, reverse=True):
        subgraph = nx.ego_graph(
            G, center_node, radius=trip_time, distance='time')
        node_points = [Point((data['x'], data['y']))
                       for node, data in subgraph.nodes(data=True)]
        bounding_poly = gpd.GeoSeries(node_points).unary_union.convex_hull
        isochrone_polys.append(bounding_poly)

    isochrone_polys = gpd.GeoDataFrame(
        geometry=isochrone_polys, crs="EPSG:4326")
    map = folium.Map(location=(place.y, place.x),
                     zoom_start=14,
                     tiles="cartodbpositron", overlay=False)
    for x in range(len(isochrone_polys)-1):
        isochrone_polys.loc[x, 'geometry'] = isochrone_polys.loc[x, 'geometry'].difference(
            isochrone_polys.loc[x+1, 'geometry'])
    isochrone_polys['color'] = colors
    for x in range(len(isochrone_polys)):
        folium.GeoJson(isochrone_polys.iloc[[x]],
                       style_function=style).add_to(map)
    return map

For instance, if we still focus on Arcivescovile in Trento, we can see its polygon isochrones by walking, driving and biking. Walking polygons seem equally distributed around the school, while driving sees polygons more rectangularly shaped due to one way streets (such as Via Perini). Whereas biking is largely distributed over Trento (Adige, Albere, San Pio X, Bolghera, San Giuseppe and Centro Storico). 

In [13]:
# Walking
get_folium_isochrone_map(get_graph(schools.loc[index, 'geometry'], "walk"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors)

In [14]:
# Driving
get_folium_isochrone_map(get_graph(schools.loc[index, 'geometry'], "drive_service"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors)

In [15]:
# Biking
get_folium_isochrone_map(get_graph(schools.loc[index, 'geometry'], "bike"),
                                   schools.loc[index, 'geometry'],
                                   trip_times, 
                                   colors)

Since it was not allowed by OSMnx to insert graph routes as layers, in the following chunk there is a function to generate route isochrones for walking, biking and driving (so three different maps). On Trentino Schools' website, the user will be able to choose the means of transport and to look at the isochrone and therefore the connectivity of the neighbourhood around a specific school. 

*Note: Sometimes it may occur a ValueError, which means that the graph network is not available, in particular for the biking type. In these cases, walking and biking plots will be the same. It has happened for few cases, in remote municipalities with few streets and no distinction between walking and biking.*

In [16]:
# Iterates over the schools and generates 3 isochrones: walk, bike and drive
def generate_route_isochrones(df):
    for index in list(df.index):

        # Configure the place, network type, trip times, and travel speed
        place = schools.loc[index, 'geometry']
        Gs = [get_graph(place, x) for x in network_type]

        import tqdm
        for i in tqdm(range(len(network_type))):
            try:
                get_folium_route_time_distance_map(Gs[i], place, trip_times, colors, index).save("../viz/isochrones/route/" +
                                                                                                 network_type[i]+"/"+str(
                                                                                                     schools.loc[index, 'index'])+".html")
            except ValueError:
                print(index)
                continue

In [ ]:
generate_route_isochrones(schools)